In [1]:
import pandas as pd

In [2]:
import re

In [3]:
# 漢数字を算用数字に直す関数 和暦を西暦に直すために元年を1年に変換する
def kanji_to_number(kanji):
    if kanji:
        kanji_map = {
            '〇': 0, '一': 1, '二': 2, '三': 3, '四': 4, '五': 5,
            '六': 6, '七': 7, '八': 8, '九': 9, '十': 10, '百': 100,
            '千': 1000, '万': 10000, '億': 100000000, '兆': 1000000000000,
        }
        result = 0
        temp = 0
        temp_10000 = 0
        current_multiplier = 1
        base_multiplier = 1

        for char in reversed(kanji):
            value = kanji_map[char]

            if value >= 10000:
                if current_multiplier > 1:
                    temp_10000 += current_multiplier
                temp += temp_10000 * base_multiplier元
                base_multiplier = value
                current_multiplier = 1
                temp_10000 = 0
            elif value >= 10:
                if current_multiplier > 1:
                    temp_10000 += current_multiplier
                current_multiplier = value
            else:
                temp_10000 += value * current_multiplier
                current_multiplier = 1
        
        if current_multiplier > 1:
            temp_10000 += current_multiplier
        temp += temp_10000 * base_multiplier
        return temp
    return None

In [4]:
# 和暦を西暦の8桁(yyyymmdd)形式に直す関数
def wareki_to_date8(wareki):
    wareki = wareki.replace('元年','一年')
    wareki_regex = re.compile('(明治|大正|昭和|平成|令和)([一二三四五六七八九十〇]+)年([一二三四五六七八九十〇]+)月([一二三四五六七八九十〇]+)日')
    match = re.findall(wareki_regex, wareki)
    if len(match)>=1:
        wareki_date = match[0]
        gengo = wareki_date[0]
        if gengo == '明治':
            gengo_nen = 1867
        elif gengo == '大正':
            gengo_nen = 1911
        elif gengo == '昭和':
            gengo_nen = 1925
        elif gengo == '平成':
            gengo_nen = 1988
        elif gengo == '令和':
            gengo_nen = 2018
        nen = kanji_to_number(wareki_date[1])
        tsuki =  kanji_to_number(wareki_date[2])
        hi =  kanji_to_number(wareki_date[3])
        
        return (gengo_nen + nen) * 10000 + tsuki * 100 + hi
    else:
        return None

In [5]:
all_law_list = pd.read_csv('./all_xml/all_law_list.csv')

In [6]:
all_law_list['公布日'] = all_law_list['公布日'].apply(wareki_to_date8)
all_law_list['改正法令公布日'] = all_law_list['改正法令公布日'].apply(wareki_to_date8)
all_law_list['施行日'] = all_law_list['施行日'].apply(wareki_to_date8)

In [7]:
all_law_list.head(5)

法令種別              法令番号                                       法令名  \
0   政令  明治五年太政官布告第三百三十七号                   明治五年太政官布告第三百三十七号（改暦ノ布告）   
1   法律    明治六年太政官布告第六十五号                    明治六年太政官布告第六十五号（絞罪器械図式）   
2   政令    明治八年太政官布告第五十四号                    明治八年太政官布告第五十四号（勲章制定ノ件）   
3   政令     明治八年太政官布告第百三号                     明治八年太政官布告第百三号（裁判事務心得）   
4   政令    明治八年太政官達第百五十二号  明治八年太政官達第百五十二号（不用物品等払下ノトキ其管庁所属ノ官吏入札禁止ノ件）   

                                         法令名読み 旧法令名       公布日 改正法令名  \
0                                     かいれきのふこく  NaN  18721109   NaN   
1                                   こうざいきかいずしき  NaN  18730220   NaN   
2                                 くんしょうせいていのけん  NaN  18750410   NaN   
3                                   さいばんじむこころえ  NaN  18750608   NaN   
4  ふようぶっぴんとうはらいさげのときそのかんちょうしょぞくのかんりにゅうさつきんしのけん  NaN  18750827   NaN   

           改正法令番号   改正法令公布日       施行日 施行日備考             法令ID  \
0             NaN  18721109  18721109   NaN  105DF0000000337   
1             NaN  18730220  18730220   NaN  106DF0000000065   
2  平成十四年政令第二百七十七号  20020812  20030501   NaN  108DF0000000054   
3             NaN  18750608  18750608   NaN  108DF0000000103   
4             NaN  18750827  18750827   NaN  108DT0000000152   

                                               本文URL  未施行  
0  https://laws.e-gov.go.jp/law/105DF0000000337/1...  NaN  
1  https://laws.e-gov.go.jp/law/106DF0000000065/1...  NaN  
2  https://laws.e-gov.go.jp/law/108DF0000000054/2...  NaN  
3  https://laws.e-gov.go.jp/law/108DF0000000103/1...  NaN  
4  https://laws.e-gov.go.jp/law/108DT0000000152/1...  NaN

In [8]:
all_law_list.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11271 entries, 0 to 11270
Data columns (total 14 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   法令種別     11271 non-null  object
 1   法令番号     11271 non-null  object
 2   法令名      11271 non-null  object
 3   法令名読み    11271 non-null  object
 4   旧法令名     496 non-null    object
 5   公布日      11271 non-null  int64 
 6   改正法令名    8079 non-null   object
 7   改正法令番号   9634 non-null   object
 8   改正法令公布日  11271 non-null  int64 
 9   施行日      11271 non-null  int64 
 10  施行日備考    820 non-null    object
 11  法令ID     11271 non-null  object
 12  本文URL    11271 non-null  object
 13  未施行      2294 non-null   object
dtypes: int64(3), object(11)
memory usage: 1.2+ MB


In [9]:
import os
import glob

In [10]:
from bs4 import BeautifulSoup

In [11]:
from tqdm.notebook import tqdm

In [12]:
from datetime import datetime

# 現在の日付を返す関数
def get_today_date():
    return int(datetime.today().strftime('%Y%m%d'))

# # 関数を実行して今日の日付を取得
# get_today_date()


In [51]:
def make_law_data(xml_data):
    # BeautifulSoupでXMLを解析
    law_list = []
    soup = BeautifulSoup(xml_data, 'xml')
    lawnum = soup.find('LawNum').text
    lawtitle = soup.find('LawTitle').text
    print(f'{" "*150}',end='\r')
    print(f'Processing...{lawtitle}',end='\r')
    for enactstatement in soup.find_all('EnactStatement'):
        if enactstatement.get_text():
            law_dict = {}
            law_dict['filename'] = filename
            law_dict['lawnum'] = lawnum
            law_dict['lawtitle'] = lawtitle
            law_dict['provision'] = 'MainProvision'
            law_dict['articlenum'] = 'EnactStatement'
            law_dict['paragraphnum'] = '0'
            law_dict['itemnum'] = '0'
            law_dict['text'] = enactstatement.get_text()
            law_list.append(law_dict)
    for preamble in soup.find_all('Preamble'):
        if preamble.get_text():
            law_dict = {}
            law_dict['filename'] = filename
            law_dict['lawnum'] = lawnum
            law_dict['lawtitle'] = lawtitle
            law_dict['provision'] = 'MainProvision'
            law_dict['articlenum'] = 'Preamble'
            law_dict['paragraphnum'] = '0'
            law_dict['itemnum'] = '0'
            law_dict['text'] = preamble.get_text()
            law_list.append(law_dict)
    for sentence in soup.find_all('Sentence'):
        law_dict = {}
        provision = sentence.find_parent('MainProvision')
        if provision:
            provision = 'MainProvision'
        else:
            provision = sentence.find_parent('SupplProvision')
            if provision and provision.get_attribute_list('AmendLawNum')[0]:
                provision = provision.get_attribute_list('AmendLawNum')[0]
            else:
                provision = 'SupplProvision'
        article = sentence.find_parent('Article')
        if article:
            articlenum = article.get_attribute_list('Num')[0]
        else:
            articlenum = '0'
        paragraph = sentence.find_parent('Paragraph')
        if paragraph:
            paragraphnum = paragraph.get_attribute_list('Num')[0]
        else:
            paragraphnum = '0'
        item = sentence.find_parent('Item')
        if item:
            itemnum = item.get_attribute_list('Num')[0]
        else:
            itemnum = '0'
            
        law_dict['filename'] = filename
        law_dict['lawnum'] = lawnum
        law_dict['lawtitle'] = lawtitle
        law_dict['provision'] = provision
        law_dict['articlenum'] = articlenum
        law_dict['paragraphnum'] = paragraphnum
        law_dict['itemnum'] = itemnum
        law_dict['text'] = sentence.get_text()
        law_list.append(law_dict)
    return law_list

In [57]:
filename = r'.\all_xml\506M60000400003_20240216_000000000000000\506M60000400003_20240216_000000000000000.xml'
with open(filename, mode='r', encoding='utf-8') as f:
    xml_data = f.read()
soup = BeautifulSoup(xml_data, 'xml')
provision = sentence.find_parent('SupplProvision')
# if provision and provision.get_attribute_list('AmendLawNum'):
#     provision = provision.get_attribute_list('AmendLawNum')[0]
# else:
#     provision = 'SupplProvision'


In [63]:
if provision and provision.get_attribute_list('AmendLawNum')[0]:
    print(True)
else:
    print(False)

False


In [55]:
print(xml_data)

<?xml version="1.0" encoding="UTF-8" standalone="no"?>
<Law Lang="ja" Era="Showa" Year="40" Num="034" PromulgateMonth="3" PromulgateDay="31" LawType="Act"><LawNum>昭和四十年法律第三十四号</LawNum><LawBody><LawTitle Kana="ほうじんぜいほう" Abbrev="" AbbrevKana="">法人税法</LawTitle>
    <EnactStatement>法人税法（昭和二十二年法律第二十八号）の全部を改正する。</EnactStatement>
    <TOC>
      <TOCLabel>目次</TOCLabel>
      <TOCPart Num="1">
        <PartTitle>第一編　総則</PartTitle>
        <TOCChapter Num="1">
          <ChapterTitle>第一章　通則</ChapterTitle>
          <ArticleRange>（第一条―第三条）</ArticleRange>
        </TOCChapter>
        <TOCChapter Num="2">
          <ChapterTitle>第二章　納税義務者</ChapterTitle>
          <ArticleRange>（第四条）</ArticleRange>
        </TOCChapter>
        <TOCChapter Num="2_2">
          <ChapterTitle>第二章の二　法人課税信託</ChapterTitle>
          <ArticleRange>（第四条の二―第四条の四）</ArticleRange>
        </TOCChapter>
        <TOCChapter Num="3">
          <ChapterTitle>第三章　課税所得等の範囲等</ChapterTitle>
          <TOCSection Num="1">
           

In [52]:
law_list = []
with tqdm(glob.glob(r'.\all_xml\**\**.xml')) as pbar:
    for filename in pbar:
        # pbar.set_description(f"Processing {filename}")
        if filename[26:34].isnumeric() and int(filename[26:34])<=get_today_date():
            with open(filename, mode='r', encoding='utf-8') as f:
                xml_data = f.read()
                law_list += make_law_data(xml_data)            


  0%|          | 0/11271 [00:00<?, ?it/s]

KeyboardInterrupt: 

In [14]:
law_sentences = pd.DataFrame(law_list)
for col in law_sentences.columns:
    law_sentences[col] = law_sentences[col].astype(str)

In [15]:
law_sentences.to_csv('law_sentences.csv',index=False)

In [41]:
law_sentences.describe()

filename        lawnum  \
count                                             3070055       3070055   
unique                                               8977          8820   
top     .\all_xml\340AC0000000033_20240612_506AC000000...  昭和四十年法律第三十三号   
freq                                                89386         89386   

       lawtitle      provision articlenum paragraphnum  itemnum     text  
count   3070055        2983777    3070055      3070055  3070055  3070055  
unique     8798          63640      15459          256     2398  1452800  
top        所得税法  MainProvision          0            1        0           
freq      89386        1550341    1164363      1313177  2159603   124184

In [25]:
# 正規表現をセットする関数
def setregex(law_text):
    search_results = {}
    synonym = {}
    # 正規表現パターン
    regex = re.compile(r'(?<=（)((?:令和|平成|昭和|大正|明治)[元一二三四五六七八九十]+年(?:法律|政令|省令|内閣府令)第[一二三四五六七八九十百千万]+号)(?:。以下「(.*?)」という。)?(?=）)')
    
    # 正規表現にマッチする部分を抽出
    matches = regex.findall(law_text)
    
    for match in matches:
        if match[0]:
            search_results[match[0]]=lawdata_list.get(match[0],match[0])
            if match[1]:
                synonym[match[0]] = match[1]
    
    # searchResultsをソート
    search_results = dict(sorted(search_results.items(), key=lambda item: len(item[1]), reverse=True))
    
    for k, v in search_results.items():
        # 省略名のマッチを探す正規表現
        synonym_regex = re.compile(f"{v}（以下「([^「]*?)」という。）")
        matches = synonym_regex.findall(law_text)
        if matches:
            synonym[k] = matches[0]
    
    
    return search_results, synonym

In [23]:
# 関連法令を探してデータに追加する関数
def make_ref_data(df, search_results, synonym):
    data = []
    for law_num in search_results:
        # 他法令の参照箇所を探す正規表現
        law_regex = re.compile(
            f"({search_results[law_num]}" +
            (f"|{synonym[law_num]}" if law_num in synonym else "") +
            ")" +
            r"((?:（(?:\d+)?。?(?:以下「[^「]*?」という。)?）)?" +
            r"第([一二三四五六七八九十百千万]+)条(?:の([一二三四五六七八九十百千万]+))?" +
            r"(?:第([一二三四五六七八九十百千万]+)項)?" + 
            r"(?:第([一二三四五六七八九十百千万]+)号)?)" 
        )

        for i, r in df.iterrows():
            matches = re.findall(law_regex, r['text'])
            for match in matches:
                referred_article_num = kanji_to_number(match[2])
                referred_article_sub_num = kanji_to_number(match[3])
                referred_paragraph_num = kanji_to_number(match[4])
                referred_item_num = kanji_to_number(match[5])

                ref_referred_data = {
                    'ref': {
                        'lawNum': r['lawnum'],
                        'lawArticle': {
                            'Provision': r['provision'],
                            'article': r['articlenum'],
                            'paragraph': r['paragraphnum'],
                            'item':r['item']
                        },
                        'text':r['text']
                    },
                    'referred': {
                        'lawNum': law_num,
                        'lawArticle': {
                            'Provision': 'MainProvision',
                            'article': f'{referred_article_num}{"_" + str(referred_article_sub_num) if referred_article_sub_num else ""}' ,
                            'paragraph': str(referred_paragraph_num),
                            'item': str(referred_item_num)
                        }
                    }
                }
                data.append(ref_referred_data)
    return data

In [27]:
data = []
for lawtitle in tqdm(law_sentences['lawtitle'].unique()):
    search_results, synonym = setregex(law_sentences.loc[law_sentences['lawtitle']==lawtitle,'text'].str.cat(sep='\n'))
    data += make_ref_data(law_sentences[law_sentences['lawtitle']==lawtitle],search_results,synonym)

  0%|          | 0/8798 [00:00<?, ?it/s]

In [28]:
data

[{'ref': {'lawNum': '明治十七年太政官布告第三十二号',
   'lawArticle': {'Provision': '平成二九年六月二一日法律第六七号',
    'article': '4',
    'paragraph': '1'},
   'text': '新組織的犯罪処罰法第十二条（刑法第四条の二に係る部分に限る。）の規定、第二条の規定による改正後の爆発物取締罰則第十条（爆発物取締罰則第四条から第六条までに係る部分に限る。）の規定、第四条の規定による改正後の暴力行為等処罰に関する法律第一条ノ三第二項の規定、第五条の規定による改正後の児童福祉法第六十条第五項（同条第一項に係る部分に限る。）の規定、第六条の規定による改正後の細菌兵器（生物兵器）及び毒素兵器の開発、生産及び貯蔵の禁止並びに廃棄に関する条約等の実施に関する法律第十一条（同法第十条に係る部分に限る。）の規定及び第七条の規定による改正後のサリン等による人身被害の防止に関する法律第八条（同法第五条第三項に係る部分に限る。）の規定は、附則第一条第一号に掲げる規定の施行の日以後に日本国について効力を生ずる条約により日本国外において犯したときであっても罰すべきものとされている罪に限り、適用する。'},
  'referred': {'lawNum': '明治四十年法律第四十五号',
   'lawArticle': {'Provision': 'MainProvision',
    'article': '4_2',
    'paragraph': 'None',
    'item': 'None'}}},
 {'ref': {'lawNum': '明治二十九年法律第八十九号',
   'lawArticle': {'Provision': '令和元年一二月一一日法律第七一号',
    'article': '0',
    'paragraph': '1'},
   'text': '第一条中外国法人の登記及び夫婦財産契約の登記に関する法律第四条の改正規定（「並びに第百三十二条」を「、第百三十二条から第百三十七条まで並びに第百三十九条」に改める部分に限る。）、第三条から第五条までの規定、第六条中商業登記法第七条の二、第十一条の二、第十五条、第十七条及び第十八条の改正規定、同法

In [30]:
ref_data = pd.json_normalize(data)

In [31]:
ref_data.to_csv('ref_data.csv',index=False)

In [33]:
ref_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 556705 entries, 0 to 556704
Data columns (total 10 columns):
 #   Column                         Non-Null Count   Dtype 
---  ------                         --------------   ----- 
 0   ref.lawNum                     556705 non-null  object
 1   ref.lawArticle.Provision       540254 non-null  object
 2   ref.lawArticle.article         556705 non-null  object
 3   ref.lawArticle.paragraph       556705 non-null  object
 4   ref.text                       556705 non-null  object
 5   referred.lawNum                556705 non-null  object
 6   referred.lawArticle.Provision  556705 non-null  object
 7   referred.lawArticle.article    556705 non-null  object
 8   referred.lawArticle.paragraph  556705 non-null  object
 9   referred.lawArticle.item       556705 non-null  object
dtypes: object(10)
memory usage: 42.5+ MB


In [34]:
ref_data.head(5)

ref.lawNum ref.lawArticle.Provision ref.lawArticle.article  \
0  明治十七年太政官布告第三十二号         平成二九年六月二一日法律第六七号                      4   
1    明治二十九年法律第八十九号         令和元年一二月一一日法律第七一号                      0   
2    明治二十九年法律第八十九号         令和元年一二月一一日法律第七一号                      0   
3    明治二十九年法律第八十九号         令和元年一二月一一日法律第七一号                      0   
4    明治二十九年法律第八十九号         令和元年一二月一一日法律第七一号                      0   

  ref.lawArticle.paragraph                                           ref.text  \
0                        1  新組織的犯罪処罰法第十二条（刑法第四条の二に係る部分に限る。）の規定、第二条の規定による改正...   
1                        1  第一条中外国法人の登記及び夫婦財産契約の登記に関する法律第四条の改正規定（「並びに第百三十二...   
2                        1  第一条中外国法人の登記及び夫婦財産契約の登記に関する法律第四条の改正規定（「並びに第百三十二...   
3                        1  第一条中外国法人の登記及び夫婦財産契約の登記に関する法律第四条の改正規定（「並びに第百三十二...   
4                        1  第一条中外国法人の登記及び夫婦財産契約の登記に関する法律第四条の改正規定（「並びに第百三十二...   

  referred.lawNum referred.lawArticle.Provision referred.lawArticle.article  \
0    明治四十年法律第四十五号                 MainProvision                         4_2   
1  昭和二十六年法律第百九十八号                 MainProvision                          94   
2  昭和二十六年法律第百九十八号                 MainProvision                         177   
3      平成十年法律第百五号                 MainProvision                          22   
4      平成十年法律第百五号                 MainProvision                         183   

  referred.lawArticle.paragraph referred.lawArticle.item  
0                          None                     None  
1                             1                     None  
2                          None                     None  
3                             2                        7  
4                             1                     None

In [37]:
ref_data[ref_data['ref.lawArticle.Provision'].isnull()]

ref.lawNum ref.lawArticle.Provision ref.lawArticle.article  \
709       大正十一年法律第七十号                     None                      3   
710       大正十一年法律第七十号                     None                      3   
711       大正十一年法律第七十号                     None                    5_3   
742       大正十一年法律第七十号                     None                      3   
743       大正十一年法律第七十号                     None                      3   
...               ...                      ...                    ...   
550770    令和六年政令第三十三号                     None                      0   
550772    令和六年政令第三十七号                     None                      0   
550911  令和六年内閣府令第二十七号                     None                      4   
551120  令和六年経済産業省令第三号                     None                      0   
551121  令和六年経済産業省令第三号                     None                      0   

       ref.lawArticle.paragraph  \
709                           1   
710                           6   
711                           1   
742                           1   
743                           6   
...                         ...   
550770                        2   
550772                        2   
550911                        1   
551120                        2   
551121                        2   

                                                 ref.text referred.lawNum  \
709     厚生労働省令で定める要件に該当するものとして厚生労働大臣の認可を受けた健康保険組合（以下この...    平成十八年法律第八十三号   
710     この場合において、同条第一号中「任意継続被保険者となった日から起算して二年を経過したとき」と...    平成十八年法律第八十三号   
711     平成二十七年度から当該一の事業年度の前々事業年度までの間において毎年度継続して協会の一般保険...    平成十八年法律第八十三号   
742     厚生労働省令で定める要件に該当するものとして厚生労働大臣の認可を受けた健康保険組合（以下この...  昭和三十三年法律第百九十二号   
743     この場合において、同条第一号中「任意継続被保険者となった日から起算して二年を経過したとき」と...  昭和三十三年法律第百九十二号   
...                                                   ...             ...   
550770  令和五年分の所得税について法第四条第一項から第三項までの規定の適用を受けるため法附則第二項の...    昭和四十年法律第三十三号   
550772  日本中央競馬会の令和四事業年度における日本中央競馬会法第二十九条の二第三項の割合を定める政令...   昭和二十九年法律第二百五号   
550911  令和八年三月三十一日までの間は、第二十条第三項の規定にかかわらず、一時保護施設には、法第十二...  昭和二十二年法律第百六十四号   
551120  法附則第六条の別に法律で定める日の前日までの間は、第二条第二項第一号及び第二号の規定の適用に...     令和五年法律第三十二号   
551121  法附則第六条の別に法律で定める日の前日までの間は、第二条第二項第一号及び第二号の規定の適用に...     令和五年法律第三十二号   

       referred.lawArticle.Provision referred.lawArticle.article  \
709                    MainProvision                          13   
710                    MainProvision                          13   
711                    MainProvision                           6   
742                    MainProvision                         8_2   
743                    MainProvision                         8_2   
...                              ...                         ...   
550770                 MainProvision                           2   
550772                 MainProvision                        29_2   
550911                 MainProvision                        12_3   
551120                 MainProvision                          54   
551121                 MainProvision                          54   

       referred.lawArticle.paragraph referred.lawArticle.item  
709                             None                     None  
710                             None                     None  
711                             None                     None  
742                                1                     None  
743                                1                     None  
...                              ...                      ...  
550770                             1                       25  
550772                             3                     None  
550911                             2                        6  
551120                             1                        1  
551121                             1                        4  

[16451 rows x 10 columns]

In [39]:
law_sentences[law_sentences['lawnum']=='令和六年経済産業省令第三号']

filename         lawnum  \
3058949  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058950  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058951  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058952  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058953  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058954  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058955  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058956  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058957  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058958  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058959  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058960  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058961  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058962  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058963  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058964  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058965  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058966  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058967  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058968  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058969  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058970  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058971  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058972  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058973  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058974  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058975  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058976  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058977  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058978  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058979  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058980  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058981  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058982  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058983  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058984  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058985  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058986  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058987  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058988  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058989  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058990  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058991  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058992  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058993  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058994  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058995  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058996  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058997  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058998  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3058999  .\all_xml\506M60000400003_20240216_00000000000...  令和六年経済産業省令第三号   
3059000  .\all_xml\506M60000400003_20240216_00